In [46]:
import numpy as np
import pandas as pd
from time import time
from sklearn import metrics
from collections import defaultdict
import matplotlib.pyplot as plt
import glob


from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.cluster import KMeans
from sklearn import preprocessing
from sklearn.metrics.cluster import contingency_matrix, homogeneity_score, completeness_score, adjusted_rand_score, adjusted_mutual_info_score, v_measure_score
from sklearn.metrics.cluster import contingency_matrix

## profiling
from pandas_profiling import ProfileReport


## Gas Turbine CO and NOx Emission Data Set

In [21]:
path = 'pp_gas_emission/'
all_files = glob.glob(path + "/*.csv")
li = []
for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    df['year'] = int(filename[-8:-4])
    li.append(df)

frame = pd.concat(li, axis=0, ignore_index=True)

## Focus on CO ?

## Standardize feature columns 

In [42]:
frame.drop('NOX',axis =1,inplace=True)

In [43]:
frame

AT      AP      AH    AFDP    GTEP     TIT     TAT     TEY     CDP  \
0      9.3779  1020.1  90.262  2.3927  19.166  1043.6  541.16  110.16  10.564   
1      9.2985  1019.9  89.934  2.3732  19.119  1039.9  538.94  109.23  10.572   
2      9.1337  1019.8  89.868  2.3854  19.178  1041.0  539.47  109.62  10.543   
3      8.9715  1019.3  89.490  2.3825  19.180  1037.1  536.89  108.88  10.458   
4      9.0157  1019.1  89.099  2.4044  19.206  1043.5  541.25  110.09  10.464   
...       ...     ...     ...     ...     ...     ...     ...     ...     ...   
36728  9.0301  1005.6  98.460  3.5421  19.164  1049.7  546.21  111.61  10.400   
36729  7.8879  1005.9  99.093  3.5059  19.414  1046.3  543.22  111.78  10.433   
36730  7.2647  1006.3  99.496  3.4770  19.530  1037.7  537.32  110.19  10.483   
36731  7.0060  1006.8  99.008  3.4486  19.377  1043.2  541.24  110.74  10.533   
36732  6.9279  1007.2  97.533  3.4275  19.306  1049.9  545.85  111.58  10.583   

            CO  year  
0       9.3472  2013  
1      11.0160  2013  
2      10.7500  2013  
3      12.2870  2013  
4       9.8229  2013  
...        ...   ...  
36728   4.5186  2011  
36729   4.8470  2011  
36730   7.9632  2011  
36731   6.2494  2011  
36732   4.9816  2011  

[36733 rows x 11 columns]

In [37]:
feature_columns = list(frame.columns)
feature_columns = list(set(feature_columns) - set(['NOX','CO','year']))

In [56]:
profile = ProfileReport(frame[feature_columns], title="frame Profiling Report",explorative=True)

In [57]:
profile

Render HTML: 100%|██████████| 1/1 [00:02<00:00,  2.29s/it]


In [38]:
frame[feature_columns].mean()

AH        77.867015
AT        17.712726
AFDP       3.925518
TIT     1081.428084
GTEP      25.563801
AP      1013.070165
CDP       12.060525
TAT      546.158517
TEY      133.506404
dtype: float64

In [39]:
frame[feature_columns].var()

AH      209.130787
AT       55.464530
AFDP      0.598976
TIT     307.524376
GTEP     17.606059
AP       41.774841
CDP       1.185475
TAT      46.817896
TEY     243.941740
dtype: float64

In [49]:
frame_feature_array = frame[feature_columns].values
scaler = preprocessing.StandardScaler()